# Sujet 5 - Analyse des dialogues dans l'Avare de Molière

## Récupérer les données

In [46]:
%matplotlib inline
import matplotlib.pyplot as plt
import pandas as pd
import re

L’Observatoire de la vie littéraire (OBVIL) promeut une approche de l'analyse des textes littéraires fondée sur le numérique. Dans le cadre du Projet Molière, des pièces de cet auteur ont été numérisées et sont accessibles librement dans différents formats utilisables par un programme informatique. Nous allons utiliser ici les textes sous format markdown accessibles [ici](http://dramacode.github.io/markdown/moliere_avare.txt).

In [2]:
data_url = 'http://dramacode.github.io/markdown/moliere_avare.txt'

Pour plus de reproductibilité, nous allons télécharger les données dans ce répertoire GitLab d'abord puis nous allons lire ce fichier plutôt que l'url directement.

In [3]:
data_file = "moliere_avare.txt"

import os
import urllib.request
if not os.path.exists(data_file):
    urllib.request.urlretrieve(data_url, data_file)

Nous pouvons regarder les premières lignes de ce fichier:

In [4]:
%load_ext rpy2.ipython

In [10]:
%%sh
head -n 55 moliere_avare.txt

---
identifier: moliere_avare  
creator: Molière.  
date: 1668  
title: L'Avare. Comédie  
---


L'AVARE,

COMÉDIE.

Par J.B.P. MOLIÈRE.

À PARIS, Chez JEAN RIBOU, au Palais, vis à vis la Porte de l'Église de la Sainte Chapelle, à l'Image Saint-Louis. M. DC. LXIX. *AVEC PRIVILÈGE DU ROI*



# ACTEURS.
 – Harpagon, Père de Cléante et d'Élise, et Amoureux de Mariane.
 – Cléante, Fils d'Harpagon, Amant de Mariane.
 – Élise, Fille d'Harpagon, Amante de Valère.
 – Valère, Fils d'Anselme, et Amant d'Élise.
 – Mariane, Amante de Cléante, et aimée d'Harpagon.
 – Anselme, Père de Valère et de Mariane.
 – Frosine, Femme d'Intrigue.
 – Maitre Simon, Courtier.
 – Maitre Jacques, Cuisinier et Cocher d'Harpagon.
 – La Flèche, Valet de Cléante.
 – Dame Claude, Servante d'Harpagon.
 – Brindavoine, laquais d'Harpagon.
 – La Merluche, laquais d'Harpagon.
 – Le commissaire, et son clerc.
La Scène est à Paris.



# L'Avare, *Comédie.*.


## Acte Premier.


### Scène Première.
Valère, Élise


    VALÈRE.
H

Comme nous pouvons le voir, les actes sont marqués par un double-dièse en début de ligne et les scènes sont marquées par un triple-dièse en début de ligne. Les dialogues de personnages ont l'air d'être sur 2 lignes : une première avec le nom du personnage en majuscule et une deuxième avec les répliques du personnage.

Nous allons tenter de réarranger les données sous forme de tableau, comme ceci :

| Personnage | Acte | Scene | Nombre de Mots | Nombre de Repliques |
|:-------|:------|:-------|:------------|:----------------|
| nom du personnage | acte dans lequel il apparait | scène dans laquelle il figure | le nombre de mots qu'il parle | le nombre de repliques |

Nous allons créer un fonction qui va remplacer les caractères à accent en caractère "normaux":

In [47]:
import unicodedata

def remove_accents(input_str):
    nfkd_form = unicodedata.normalize('NFKD', input_str)
    return u"".join([c for c in nfkd_form if not unicodedata.combining(c)])

Comme nous pouvons le voir, il y a quelques discordances entre la liste des personnages énumérés en-dessous du numéro de scène et les répliques dans le dialogue.

In [84]:
acte = 0
scene = 0
infos_scene = {}

data = []
with open(data_file) as f:
    lines = f.readlines()
nbline = 0
while nbline < len(lines):
    line = lines[nbline]
    if line.startswith("## Acte"):
        acte += 1
    elif line.startswith("### Sc"):
        if infos_scene:
            data += infos_scene.values()
        scene += 1
        nbline += 1
        line = lines[nbline]
        if line.strip():
            infos_scene = {l.strip().upper():{'acte':acte,'scene':scene,'personnage':l.strip().upper(),'nombre_de_mots':0,'nombre_de_repliques':0} for l in remove_accents(line.strip()).split(",")}
        else:
            infos_scene = {}
            print("No characters listed for scene",scene,"acte",acte)
    elif re.search(r"^    [A-ZÈÉ ]+.$",line):
        assert acte and scene
        personnage = remove_accents(re.search(r"^    ([A-ZÈÉ ]+).$",line).groups()[0])
        nbline += 1
        line = lines[nbline]
        assert line.strip() # check line is not empty
        nombre_de_mots = len(line.split()) # on va supposer que la ponctuation est négligeable dans le compte
        if personnage not in infos_scene:
            print(personnage,"is not listed under scene",scene,"acte",acte,"but is speaking")
            infos_scene[personnage] = {'acte':acte,'scene':scene,'personnage':personnage,'nombre_de_mots':0,'nombre_de_repliques':0}
        infos_scene[personnage]['nombre_de_repliques'] += 1
        infos_scene[personnage]['nombre_de_mots'] += nombre_de_mots
    nbline += 1
df = pd.DataFrame(data)
df

VALERE is not listed under scene 19 acte 3 but is speaking
No characters listed for scene 26 acte 4
HARPAGON is not listed under scene 26 acte 4 but is speaking


acte  nombre_de_mots  nombre_de_repliques      personnage  scene
0       1             596                    8          VALERE      1
1       1             473                    8           ELISE      1
2       1             725                   10         CLEANTE      2
3       1             150                    9           ELISE      2
4       1             396                   34        HARPAGON      3
5       1             242                   32       LA FLECHE      3
6       1             147                   23           ELISE      4
7       1             211                   29         CLEANTE      4
8       1            1044                   53        HARPAGON      4
9       1             621                   22          VALERE      5
10      1             238                   20        HARPAGON      5
11      1              36                    4           ELISE      5
12      2             350                   21         CLEANTE      6
13      2             853                   20       LA FLECHE      6
14      2               0                    0    MAITRE SIMON      7
15      2             159                    9        HARPAGON      7
16      2             126                    6         CLEANTE      7
17      2              13                    1       LA FLECHE      7
18      2               1                    1         FROSINE      8
19      2              21                    1        HARPAGON      8
20      2             281                    6       LA FLECHE      9
21      2             116                    5         FROSINE      9
22      2             520                   35        HARPAGON     10
23      2            1234                   35         FROSINE     10
24      3             557                   34        HARPAGON     11
25      3              74                    3         CLEANTE     11
26      3               3                    1           ELISE     11
27      3             247                   11          VALERE     11
28      3               0                    0     DAME CLAUDE     11
29      3               0                    0  MAITRE JACQUES     11
..    ...             ...                  ...             ...    ...
82      4              11                    1        HARPAGON     26
83      5              87                    6        HARPAGON     27
84      5             104                    7  LE COMMISSAIRE     27
85      5               0                    0       SON CLERC     27
86      5               0                    0  MAITRE JACQUES     28
87      5             172                   19        HARPAGON     28
88      5             154                    8  LE COMMISSAIRE     28
89      5               0                    0       SON CLERC     28
90      5             611                   30          VALERE     29
91      5             434                   30        HARPAGON     29
92      5               0                    0  LE COMMISSAIRE     29
93      5               0                    0       SON CLERC     29
94      5               0                    0  MAITRE JACQUES     29
95      5              10                    1           ELISE     30
96      5               0                    0         MARIANE     30
97      5               4                    1         FROSINE     30
98      5             124                    4        HARPAGON     30
99      5              20                    1          VALERE     30
100     5               0                    0  MAITRE JACQUES     30
101     5               0                    0  LE COMMISSAIRE     30
102     5               0                    0       SON CLERC     30
103     5             383                   14         ANSELME     31
104     5             245                   11        HARPAGON     31
105     5               0                    0           ELISE     31
106     5             190                    3         MARIANE     31
107     5      

Voyons voir s'il y a bien le bon nombre d'Actes et de Scènes:

In [85]:
%%sh
grep -c "## Acte" moliere_avare.txt
grep -c "### Scène" moliere_avare.txt

5
32


In [86]:
df.acte.value_counts().shape

(5,)

In [87]:
df.scene.value_counts().shape

(31,)

In [88]:
df.personnage.value_counts().shape

(15,)

On voit donc qu'on retrouve le même nombre d'actes et de scènes qu'avec l'analyse de texte via `grep`. On retrouve aussi les 15 personnages listées en début de document.

In [90]:
print("".join(lines[19:33]))

 – Harpagon, Père de Cléante et d'Élise, et Amoureux de Mariane.
 – Cléante, Fils d'Harpagon, Amant de Mariane.
 – Élise, Fille d'Harpagon, Amante de Valère.
 – Valère, Fils d'Anselme, et Amant d'Élise.
 – Mariane, Amante de Cléante, et aimée d'Harpagon.
 – Anselme, Père de Valère et de Mariane.
 – Frosine, Femme d'Intrigue.
 – Maitre Simon, Courtier.
 – Maitre Jacques, Cuisinier et Cocher d'Harpagon.
 – La Flèche, Valet de Cléante.
 – Dame Claude, Servante d'Harpagon.
 – Brindavoine, laquais d'Harpagon.
 – La Merluche, laquais d'Harpagon.
 – Le commissaire, et son clerc.



## Analyser les données